In [1]:
from gensim.models import KeyedVectors
import matplotlib.pyplot as plt
from keras.preprocessing.text import *

import nltk
import numpy as np
nltk.download('treebank')
nltk.download('universal_tagset')
from nltk.corpus import treebank
from sklearn.model_selection import train_test_split
from keras.models import Sequential
from keras.layers import Embedding
from keras.layers import GRU
from keras.layers import TimeDistributed
from keras.layers import Dense
from keras.utils import to_categorical
from keras.preprocessing.sequence import pad_sequences
import json

[nltk_data] Downloading package treebank to
[nltk_data]     C:\Users\Rahul\AppData\Roaming\nltk_data...
[nltk_data]   Package treebank is already up-to-date!
[nltk_data] Downloading package universal_tagset to
[nltk_data]     C:\Users\Rahul\AppData\Roaming\nltk_data...
[nltk_data]   Package universal_tagset is already up-to-date!


**Loading the data**

General Function for getting train_test_val

In [2]:
def create_train_test_val(file):
    lst_out_text=[]
    lst_out_labels=[]
    for i in file.values():
        lst =[]
        sentence = i['text']
        labels = i['labels']
        lst = sentence.split()
        lst_out_text.append(lst)
        lst_out_labels.append(labels)
    return lst_out_text,lst_out_labels    

Reading ATE JSON Files

In [3]:
ATE_train = None
ATE_test = None
ATE_val = None
with open("Task1\processed\ATE_train.json") as f1:
    ATE_train  = json.load(f1)

with open("Task1\processed\ATE_test.json") as f2:
    ATE_test = json.load(f2)

with open("Task1\processed\ATE_val.json") as f3:
    ATE_val = json.load(f3)


Reading NER JSON Files

In [4]:
NER_train = None
NER_test = None
NER_val = None
with open("Task1\processed\\NER_train.json") as f1:
    NER_train  = json.load(f1)

with open("Task1\processed\\NER_test.json") as f2:
    NER_test = json.load(f2)

with open("Task1\processed\\NER_val.json") as f3:
    NER_val = json.load(f3)


ATE_Dataset

In [5]:
X_train_ate,Y_train_ate= create_train_test_val(ATE_train)
X_test_ate,Y_test_ate = create_train_test_val(ATE_test)
X_val_ate,Y_val_ate = create_train_test_val(ATE_val)

print(X_train_ate)
print(Y_train_ate)



[['I', 'charge', 'it', 'at', 'night', 'and', 'skip', 'taking', 'the', 'cord', 'with', 'me', 'because', 'of', 'the', 'good', 'battery', 'life', '.'], ['it', 'is', 'of', 'high', 'quality', ',', 'has', 'a', 'killer', 'GUI', ',', 'is', 'extremely', 'stable', ',', 'is', 'highly', 'expandable', ',', 'is', 'bundled', 'with', 'lots', 'of', 'very', 'good', 'applications', ',', 'is', 'easy', 'to', 'use', ',', 'and', 'is', 'absolutely', 'gorgeous', '.'], ['Easy', 'to', 'start', 'up', 'and', 'does', 'not', 'overheat', 'as', 'much', 'as', 'other', 'laptops', '.'], ['Great', 'laptop', 'that', 'offers', 'many', 'great', 'features', '!'], ['One', 'night', 'I', 'turned', 'the', 'freaking', 'thing', 'off', 'after', 'using', 'it', ',', 'the', 'next', 'day', 'I', 'turn', 'it', 'on', ',', 'no', 'GUI', ',', 'screen', 'all', 'dark', ',', 'power', 'light', 'steady', ',', 'hard', 'drive', 'light', 'steady', 'and', 'not', 'flashing', 'as', 'it', 'usually', 'does', '.'], ['However', ',', 'the', 'multi-touch', 'g

NER_Dataset

In [6]:
X_train_ner,Y_train_ner = create_train_test_val(NER_train)
X_test_ner,Y_test_ner = create_train_test_val(NER_test)
X_val_ner,Y_val_ner = create_train_test_val(NER_val)

print(X_train_ner)
print(Y_train_ner)

[['Therefore,', 'while', 'interpreting', 'statutory', 'provisions,', 'the', 'courts', 'should', 'keep', 'in', 'mind', 'the', 'objectives', 'or', 'purpose', 'for', 'which', 'statute', 'has', 'been', 'enacted.'], ['The', 'petitioner', 'in', 'W.P.No.15821', 'of', '2008', 'was', 'never', 'considered', 'for', 'appointment', 'under', 'the', 'National', 'Rural', 'Employment', 'Guarantee', 'Scheme', 'either', 'through', 'Employment', 'Exchange', 'sponsorship', 'or', 'by', 'Outsourcing', 'Agencies.'], ['The', 'factum', 'of', 'accident,', 'allegation', 'of', 'rash', 'and', 'negligent', 'driving', 'causing', 'death', 'of', 'Sukendra', 'Pal', 'Singh', 'were', 'denied.'], ['..36..', 'W.A.No.655/2012', '&', 'others', 'Meaning', 'thereby', 'that', 'except', 'interview', 'by', 'the', 'Commission,', 'entire', 'procedure', 'for', 'recruitment', 'as', 'emergency', 'appointment', 'was', 'followed.'], ['The', 'law', 'on', 'this', 'issue', 'is', 'well', 'settled', 'and', 'the', 'law', 'is', 'that', 'though'

In [7]:
model = KeyedVectors.load_word2vec_format('WordEmbeddings/Word2Vec.bin',binary=True)

In [8]:
def TokenCreator(sentences,tokenizer=None):
    
    temp_wordlist = None
    if(tokenizer == None):
        tokenizer2 = Tokenizer()
        tokenizer2.fit_on_texts(sentences)
        
        temp_wordlist = tokenizer2.texts_to_sequences(sentences)
        return (temp_wordlist,tokenizer2)
    
    else:
        temp_wordlist = tokenizer.texts_to_sequences(sentences)
        return (temp_wordlist,tokenizer)
    


In [18]:
def find_vocab_size(dataset):
    lst=[]
    for i in dataset:
        for j in i:
            lst.append(j)
    st = set(lst)
    return st

In [16]:
X_train_ate_tokenized, toke = TokenCreator(X_train_ate)
X_test_ate_tokenized = TokenCreator(X_test_ate, tokenizer = toke)
X_val_ate_tokenized = TokenCreator(X_val_ate, tokenizer = toke)
Y_train_ate_tokenized,toke2 = TokenCreator(Y_train_ate)
Y_test_ate_tokenized = TokenCreator(Y_test_ate, tokenizer = toke2)
Y_val_ate_tokenized = TokenCreator(Y_val_ate, tokenizer = toke2)

# print(X_test_ate_tokenized)
# print(X_val_ate_tokenized)
# print(X_test_ate_tokenized)


([[18, 1, 2025, 3, 354, 457, 32, 18, 9, 131, 30, 15, 85, 164, 305, 75, 1, 1390, 906, 382, 15, 103, 5, 3, 79, 5, 320, 3, 648, 1, 4, 24, 5, 41, 21, 36, 2], [16, 28, 899, 160, 4, 55, 109, 8, 26, 40], [620, 847, 2211, 22, 1, 783, 2302, 579, 1, 86, 52, 4, 1, 23, 1698, 265, 2], [1, 373, 13, 15, 54, 640, 206, 195, 2347, 20, 45, 9, 342, 1, 324, 10, 16, 120, 2], [5, 1086, 104, 4, 47, 5, 90, 5, 42, 868, 222, 2], [5, 42, 30, 94, 355, 6, 440, 304, 1, 189, 86, 3, 6, 244, 621, 3, 4, 5, 173, 9, 182, 315, 40], [7, 113, 176, 1, 268, 756, 273, 261, 8, 70, 2], [1, 33, 53, 368, 6, 37, 21, 70, 3, 4, 25, 34, 80, 345, 12, 5, 2], [20, 1, 1046, 124, 2221, 22, 7, 107, 19, 770, 18, 661, 393, 1089, 2], [60, 75, 9, 286, 7, 488, 188, 5, 116, 4, 17, 452, 13, 1, 332, 34, 407, 4, 30, 27, 415, 9, 93, 332, 2], [5, 17, 222, 3, 1719, 52, 3, 4, 43, 34, 334, 165, 60, 50, 264, 140, 40], [340, 3, 1, 23, 17, 243, 462, 3, 207, 500, 56, 1, 505, 28, 3, 4, 17, 262, 18, 24, 2], [62, 8, 26, 3, 21, 689, 11, 39, 1, 577, 13, 7, 59, 2],

In [22]:
st1 = find_vocab_size(X_train_ate)
st2 = find_vocab_size(X_test_ate)

print(len(st2-st1))
print(len(st2))
print(len(st1))

451
1324
2740


In [11]:
vocab_size_ate = find_vocab_size(X_train_ate)
vocab_size_ate

2740

In [12]:
embedding_weight = np.zeros((vocab_size_ate, 300))

word2id = toke.word_index

In [13]:
for word, index in word2id.items():
    try:
        embedding_weight[index:] = model[word]
    except KeyError:
        pass

In [14]:
MAX_SEQ_LENGTH = 100  # sequences greater than 100 in length will be truncated

X_padded = pad_sequences(X_train_ate_tokenized, maxlen=MAX_SEQ_LENGTH, padding="pre", truncating="post")
Y_padded = pad_sequences(Y_train_ate_tokenized, maxlen=MAX_SEQ_LENGTH, padding="pre", truncating="post")

X_padded_test = pad_sequences(X_test_ate_tokenized, maxlen=MAX_SEQ_LENGTH, padding="pre", truncating="post")
Y_padded_test = pad_sequences(Y_test_ate_tokenized, maxlen=MAX_SEQ_LENGTH, padding="pre", truncating="post")

# X_padded_val = pad_sequences(X_val_ate_tokenized, maxlen=MAX_SEQ_LENGTH, padding="pre", truncating="post")
# Y_padded_val = pad_sequences(Y_val_ate_tokenized, maxlen=MAX_SEQ_LENGTH, padding="pre", truncating="post")

ValueError: setting an array element with a sequence. The requested array has an inhomogeneous shape after 1 dimensions. The detected shape was (328,) + inhomogeneous part.

In [ ]:
Y_padded[0]
Y_padded.shape

(906, 100)

In [ ]:
Y_padded = to_categorical(Y_padded)
# can change to label based encoding

array([[[1., 0., 0., 0.],
        [1., 0., 0., 0.],
        [1., 0., 0., 0.],
        ...,
        [0., 0., 1., 0.],
        [0., 0., 0., 1.],
        [0., 1., 0., 0.]],

       [[1., 0., 0., 0.],
        [1., 0., 0., 0.],
        [1., 0., 0., 0.],
        ...,
        [0., 1., 0., 0.],
        [0., 1., 0., 0.],
        [0., 1., 0., 0.]],

       [[1., 0., 0., 0.],
        [1., 0., 0., 0.],
        [1., 0., 0., 0.],
        ...,
        [0., 1., 0., 0.],
        [0., 1., 0., 0.],
        [0., 1., 0., 0.]],

       ...,

       [[1., 0., 0., 0.],
        [1., 0., 0., 0.],
        [1., 0., 0., 0.],
        ...,
        [0., 1., 0., 0.],
        [0., 1., 0., 0.],
        [0., 1., 0., 0.]],

       [[1., 0., 0., 0.],
        [1., 0., 0., 0.],
        [1., 0., 0., 0.],
        ...,
        [0., 0., 0., 1.],
        [0., 0., 0., 1.],
        [0., 1., 0., 0.]],

       [[1., 0., 0., 0.],
        [1., 0., 0., 0.],
        [1., 0., 0., 0.],
        ...,
        [0., 1., 0., 0.],
        [0., 1.

In [ ]:
X_padded.shape

(906, 100)

In [ ]:
Y_padded.shape


(906, 100, 4)

<a href="https://www.kaggle.com/code/tanyadayanand/pos-tagging-using-rnn#1.-Preprocess-data"> Reference </a>

In [ ]:
gru_model = Sequential()
gru_model.add(Embedding(input_dim = vocab_size_ate,
                        output_dim = 300,
                        input_length  = 100,
                        weights = [embedding_weight],
                        ))

gru_model.add(GRU(64, return_sequences=True))
gru_model.add(TimeDistributed(Dense(Y_padded.shape[2], activation='softmax')))

In [ ]:
gru_model.compile(loss='categorical_crossentropy',
              optimizer='adam',
              metrics=['acc'])

In [ ]:
gru_model.summary()

Model: "sequential_6"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding_6 (Embedding)     (None, 100, 300)          822000    
                                                                 
 gru_5 (GRU)                 (None, 100, 64)           70272     
                                                                 
 time_distributed_5 (TimeDi  (None, 100, 4)            260       
 stributed)                                                      
                                                                 
Total params: 892532 (3.40 MB)
Trainable params: 892532 (3.40 MB)
Non-trainable params: 0 (0.00 Byte)
_________________________________________________________________


In [ ]:
gru_training = gru_model.fit(X_padded, Y_padded, batch_size=128, epochs=5, validation_data=(X_padded_val, Y_padded_val))

ValueError: Failed to find data adapter that can handle input: (<class 'list'> containing values of types {'(<class \'list\'> containing values of types {"<class \'int\'>"})'}), <class 'numpy.ndarray'>